In [7]:
from transformers import AutoModelForCTC, Wav2Vec2Processor
from datasets import load_dataset, load_metric, Audio
import numpy as np
import torch

In [27]:
# model = AutoModelForCTC.from_pretrained(".").to('cuda')
# processor = Wav2Vec2Processor.from_pretrained(".")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [39]:
model = AutoModelForCTC.from_pretrained("vitouphy/xls-r-300m-km").to('cuda')
processor = Wav2Vec2Processor.from_pretrained("vitouphy/xls-r-300m-km")

Downloading:   0%|          | 0.00/2.02k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.18G [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/214 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/260 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/795 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/309 [00:00<?, ?B/s]

In [3]:
common_voice_test = load_dataset('csv', data_files='km_kh_male/line_index_test.csv', split = 'train')

Using custom data configuration default-fbad308ab5a03eb2
Reusing dataset csv (/workspace/.cache/huggingface/datasets/csv/default-fbad308ab5a03eb2/0.0.0/6b9057d9e23d9d8a2f05b985917a0da84d70c5dae3d22ddd8a3f22fb01c69d9e)


In [4]:
common_voice_test  = (common_voice_test
                      .remove_columns(["Unnamed: 0", "drop"])
                      .rename_column('text', 'sentence'))

In [5]:
common_voice_test  = common_voice_test.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')

In [8]:
common_voice_test[0]

{'audio': {'path': '/workspace/xls-r-300m-km/km_kh_male/wavs/khm_1443_3799144408.wav',
  'array': array([-1.0600963e-06,  1.2359066e-06, -1.4001107e-06, ...,
         -3.1423504e-05,  4.4914182e-06,  0.0000000e+00], dtype=float32),
  'sampling_rate': 16000},
 'sentence': 'ស៊ី ដាច់ ម៉ូតូ នៅ ពេល ដែល ប្រើ ឱ្យ ឌុប សម្ភារៈ គ្រឿង សង្ហារឹម យក ទៅ ឱ្យ ម៉ូយ នៅ ម្ដុំ វត្ដ សំរោងអណ្ដែត'}

In [11]:
def prepare_dataset(batch):
    audio = batch["audio"]
    
    # batched output is "un-batched"
    batch["input_values"] = processor(np.array(audio["array"]), sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [12]:
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names)

0ex [00:00, ?ex/s]

In [45]:
i = 21

In [46]:
input_dict = processor(common_voice_test[i]["input_values"], return_tensors="pt", padding=True)
logits = model(input_dict.input_values.to("cuda")).logits
pred_ids = torch.argmax(logits, dim=-1)[0]

It is strongly recommended to pass the ``sampling_rate`` argument to this function. Failing to do so can result in silent errors that might be hard to debug.


In [47]:
print("Prediction:")
pred_ids = pred_ids[pred_ids != processor.tokenizer.pad_token_id]
print(processor.decode(pred_ids))

print("\nReference:")
print(processor.decode(common_voice_test['labels'][i]))
# print(common_voice_test_transcription[0]["sentence"].lower())

Prediction:
កាបូហ្វូនរ៉ាន និង កូហ្វាកទ័រ ជា មិត្ត និង គ្នា

Reference:
កាបូហ្វូនរ៉ាន និង កូហ្វាក់ទ័រ ជា មិត្ត និង គ្នា
